In [3]:
import os
import tensorflow as tf
import itertools
import numpy as np
from numpy import unravel_index
from random import choice, random, sample
from operator import itemgetter
np.random.seed(1337)  # for reproducibility
from keras.models import Sequential, Model, load_model
from keras.layers import Input, BatchNormalization, Reshape
from keras.layers import Dense, Dropout, Activation, Flatten, LocallyConnected2D
from keras.layers import Conv2D, MaxPooling2D, AlphaDropout, ConvLSTM2D, AvgPool2D, Conv2DTranspose, UpSampling2D
from keras.layers import add, concatenate, multiply
from keras.initializers import VarianceScaling, RandomUniform
from keras.optimizers import Adam, SGD, rmsprop
from keras.preprocessing.image import ImageDataGenerator
from keras.utils import np_utils, multi_gpu_model
from keras.utils.vis_utils import plot_model
from keras.engine.topology import Container
from keras.optimizers import SGD, Adadelta, Adagrad
from keras.regularizers import l1, l2
import keras.backend as K
K.set_image_dim_ordering('th')

from keras.callbacks import Callback, ReduceLROnPlateau, LearningRateScheduler, TensorBoard, ModelCheckpoint
import matplotlib.pyplot as plt
import time
%matplotlib notebook

Using TensorFlow backend.


In [4]:
class Ataxx:
    def __init__(self, board=None):
        if board is None:                  # if there is no initialization given
            self.data = np.zeros((7, 7))   # then generate a board with starting init, and black(-1) takes first turn
            self.data[0, 0] = -1           
            self.data[6, 6] = -1
            self.data[0, 6] = 1
            self.data[6, 0] = 1
        else:
            self.data = board
            
    def get_feature_map(self, turn):
        friendly_map = (self.data == turn).astype(float)
        opponent_map = (self.data == -turn).astype(float)
        return np.concatenate((friendly_map.reshape((1, 7, 7)), opponent_map.reshape((1, 7, 7))), axis=0)
    
    def get_mask(self, turn, init=0.001):   # zero(init) out all illegal move positions
        moves = self.get_moves(turn)
        moves = list(zip(*self.get_moves(turn)))
        if len(moves) == 0:
            return np.zeros((2, 7, 7))
        else:
            start_pos = tuple(zip(*moves[0]))
            end_pos = tuple(zip(*moves[1]))
            start_mask = np.ones((7, 7)) * init
            start_mask[start_pos] = 1
            end_mask = np.ones((7, 7)) * init
            end_mask[end_pos] = 1
            return np.concatenate((start_mask.reshape((1, 7, 7)), end_mask.reshape((1, 7, 7))), axis=0)
    
    def plot(self, is_next_move=False, turn=None):                        # plot the board
        image = self.data.copy()
        if is_next_move:
            if turn not in [-1, 1]:
                raise ValueError("Turn must be -1 or 1, or Must input a turn for next moves")
            else:
                next_moves = self.get_moves(turn)
                if len(next_moves) == 0:
                    raise ValueError("Game is over already")
                next_pos = list(zip(*next_moves))[1]
                for pos in next_pos:
                    image[pos] = turn / 2
        plt.imshow(image, cmap='gray')
        plt.xticks(range(7), range(7))
        plt.yticks(range(7), range(7))
        plt.show()
                
    def is_valid(self, turn, pos):
        if turn not in [-1, 1]:
            raise ValueError("Turn must be -1 or 1") 
        elif self.data[pos] != 0:
            return False
        else:
            for dr in range(-2, 3):
                for dc in range(-2, 3):
                    pos_tmp = (pos[0]+dr, pos[1]+dc)
                    if pos_tmp[0] >= 0 and pos_tmp[1] >= 0 and pos_tmp[0] < 7 and pos_tmp[1] < 7:
                        if self.data[pos_tmp] == turn:  # convert any piece of the opponent to 'turn'
                            return True
            return False
        
    def get_moves(self, turn):
        if turn not in [-1, 1]:
            raise ValueError("Turn must be -1 or 1")
        else:
            next_moves = []
            for r in range(7):
                for c in range(7):
                    has_duplicate_move = False      # move within the radius of one of another friendly piece is called
                    if self.is_valid(turn, (r, c)): # duplicate move
                        for dr in range(-2, 3):
                            for dc in range(-2, 3):
                                if abs(dr) <= 1 and abs(dc) <=1 and has_duplicate_move: 
                                    continue        # no need to record same move again
                                else:
                                    pos_tmp = (r+dr, c+dc)
                                    if pos_tmp[0] >= 0 and pos_tmp[1] >= 0 and pos_tmp[0] < 7 and pos_tmp[1] < 7:
                                        if self.data[pos_tmp] == turn:
                                            next_moves.append((pos_tmp, (r, c)))
            return next_moves
    
    def get_greedy_move(self, turn):
        moves = self.get_moves(turn)
        if len(moves) == 0:
            raise ValueError('No Possible Moves')
        store_data = self.data.copy()
        best_score = -1000000
        for move in moves:
            self.data = store_data.copy()
            self.move_to(turn, move[0], move[1])
            score = self.evaluate(turn, -turn)
            if score > best_score:
                best_move = move
                best_score = score
        self.data = store_data
        return best_move
        
    def move_to(self, turn, pos0, pos1):
        if turn not in [-1, 1]:
            raise ValueError("Turn must be -1 or 1") 
        elif not self.is_valid(turn, pos1):
            raise ValueError("This move: " + str((pos0, pos1)) + " of turn: " + str(turn) + " is invalid") 
        elif self.data[pos0] != turn:
            raise ValueError("The starting position is not your piece")
        else:
            dis = np.array(pos1) - np.array(pos0)    # check if is jump move or duplicate move
            if abs(dis[0]) > 1 or abs(dis[1]) > 1:   # jump move
                self.data[pos0] = 0
                self.data[pos1] = turn
            else:                                    # duplicate move
                self.data[pos1] = turn
            for dr in range(-1, 2):                  # infection mode!!!!
                for dc in range(-1, 2):
                    pos_tmp = (pos1[0]+dr, pos1[1]+dc)
                    if pos_tmp[0] >= 0 and pos_tmp[1] >= 0 and pos_tmp[0] < 7 and pos_tmp[1] < 7:
                        if self.data[pos_tmp] == -turn:  # convert any piece of the opponent to 'turn'
                            self.data[pos_tmp] = turn
                            
    def simu_move_to(self, turn, pos0, pos1):
        if turn not in [-1, 1]:
            raise ValueError("Turn must be -1 or 1") 
        elif not self.is_valid(turn, pos1):
            raise ValueError("This move: " + str((pos0, pos1)) + " of turn: " + str(turn) + " is invalid") 
        elif self.data[pos0] != turn:
            raise ValueError("You are not moving your piece")
        else:
            tmp_data = self.data.copy()
            dis = np.array(pos1) - np.array(pos0)    # check if is jump move or duplicate move
            if abs(dis[0]) > 1 or abs(dis[1]) > 1:   # jump move
                tmp_data[pos0] = 0
                tmp_data[pos1] = turn
            else:                                    # duplicate move
                tmp_data[pos1] = turn
            for dr in range(-1, 2):                  # infection mode!!!!
                for dc in range(-1, 2):
                    pos_tmp = (pos1[0]+dr, pos1[1]+dc)
                    if pos_tmp[0] >= 0 and pos_tmp[1] >= 0 and pos_tmp[0] < 7 and pos_tmp[1] < 7:
                        if tmp_data[pos_tmp] == -turn:  # convert any piece of the opponent to 'turn'
                            tmp_data[pos_tmp] = turn
            return tmp_data
    
    def evaluate(self, turn, this_turn, max_score=100, min_score=0.1):
        if turn not in [-1, 1]:
            raise ValueError("Turn must be -1 or 1") 
        else:
            turn_no = 0
            op_no = 0
            for r in range(7):
                for c in range(7):
                    if self.data[r, c] == turn:
                        turn_no += 1
                    elif self.data[r, c] == -turn:
                        op_no += 1
            if turn_no + op_no == 49:
                if turn_no > op_no:
                    return max_score
                else:
                    return -max_score
            else:
                if len(self.get_moves(this_turn)) == 0:# if one of them can no longer move, count and end
                    if turn_no > op_no:
                        return max_score
                    else:
                        return -max_score
                else:
                    value = turn_no - op_no
            return value * min_score

In [5]:
class Relay():
    def __init__(self, max_size):
        self.relay = []
        self.max_size = max_size

    def reset(self):
        self.relay = []
        
    def add_sample(self, new_sample):
        if len(self.relay) >= self.max_size:
            self.relay.pop(0)
        self.relay.append(new_sample)
    
    def get_batch(self, batch_size):
        if len(self.relay) < batch_size:
            print('not enough sample')
            raise ValueError('relay not large enough')
        else:
            batch = sample(self.relay, batch_size)
            # generate random array to decide the orientation of the data augmentation
            is_flip = np.random.random(batch_size) < 0.5
            rot_times = (np.random.random(batch_size) * 4).astype(int)
            
            cur_state = np.array([self.augmentation(item[0], is_flip[i], rot_times[i]) 
                                  for i, item in enumerate(batch)]).reshape(-1, 2, 7, 7)
            cur_mask = np.array([self.augmentation(item[1], is_flip[i], rot_times[i])
                                 for i, item in enumerate(batch)]).reshape(-1, 2, 7, 7)
            cur_action = np.array([self.augmentation(item[2], is_flip[i], rot_times[i])
                                   for i, item in enumerate(batch)]).reshape(-1, 2, 7, 7)
            try:
                cur_reward = np.array([item[3] for item in batch]).reshape(-1)
                new_state = np.array([self.augmentation(item[4], is_flip[i], rot_times[i])
                                      for i, item in enumerate(batch)]).reshape(-1, 2, 7, 7)
                new_mask = np.array([self.augmentation(item[5], is_flip[i], rot_times[i])
                                      for i, item in enumerate(batch)]).reshape(-1, 2, 7, 7)
            except:
                cur_reward = None
                new_state = None
                new_mask = None
            return cur_state, cur_mask, cur_action, cur_reward, new_state, new_mask
    
    def augmentation(self, data, is_flip, rot_time): # data must have three dimentions and depth first
        if data is None:
            return None
        else:
            if is_flip:
                data = np.fliplr(data)
            data = np.rot90(data, k=rot_time, axes=(1, 2))
            return data
    
    def size(self):
        return len(self.relay)

# BatchNormalization helps in hard-to-tune lr situations

In [15]:
def neg_log_loss(y_true, y_pred):
    y_true = K.reshape(y_true, (-1, 1, 98))
    y_pred = K.reshape(y_pred, (-1, 1, 98))
    y_log = K.log(y_pred)
    y_concate = K.concatenate([y_true, y_log], axis=1)
    y_prod = K.prod(y_concate, axis=1)
    return -K.sum(y_prod)


class CriticNetwork(object):
    def __init__(self, TAU=0.001, LEARNING_RATE=0):
        self.TAU = TAU
        self.LEARNING_RATE = LEARNING_RATE

        #Now create the model
        with tf.device("/cpu:0"):
            self.model = self.create_critic_network() 
            self.target_model = self.create_critic_network() 
            self.target_model.set_weights(self.model.get_weights())
        
        try:
            self.target_model.load_weights("pretrained_critic_model.h5")
            self.pretrained = True
        except:
            self.pretrained = False
        
    def target_train(self):
        critic_weights = self.model.get_weights()
        critic_target_weights = self.target_model.get_weights()
        for i in range(len(critic_weights)):
            critic_target_weights[i] = self.TAU * critic_weights[i] + (1 - self.TAU)* critic_target_weights[i]
        self.target_model.set_weights(critic_target_weights)
        
    def save_target_pretrain(self):
        self.target_model.save_weights("pretrained_critic_model.h5")

    def create_critic_network(self):
        board_input = Input(shape=(2, 7, 7))
        x = Conv2D(32, (1, 1), activation='relu', padding='same')(board_input)
        x = BatchNormalization(axis=1)(x)
        board_feature = MaxPooling2D((2, 2))(x)

        action_input = Input(shape=(2, 7, 7))
        x = Conv2D(32, (1, 1), activation='relu', padding='same')(action_input)
        x = BatchNormalization(axis=1)(x)
        action_feature = MaxPooling2D((2, 2))(x)
        
        overall_feature = concatenate([board_input, action_input], axis=1)
        x = Conv2D(64, (3, 3), activation='relu', padding='same')(overall_feature)
        x = BatchNormalization(axis=1)(x)
        x = MaxPooling2D((2, 2))(x)
        
        x = Conv2D(128, (3, 3), activation='relu', padding='same')(x)
        x = BatchNormalization(axis=1)(x)
        x = Conv2D(128, (3, 3), activation='relu', padding='same')(x)
        x = BatchNormalization(axis=1)(x)
        x = Flatten()(x)
        
        x = Dense(256, activation='relu')(x)
        x = BatchNormalization(axis=1)(x)
        x = Dense(1)(x)
        # construct model
        model = Model(inputs=[board_input, action_input], outputs=[x])
        print("actor")
        print(model.summary())
        # sgd = SGD(lr=self.LEARNING_RATE, decay=1e-6, momentum=0.9, nesterov=True)
        model.compile(loss='mse', optimizer=Adam(lr=self.LEARNING_RATE, decay=1e-6), metrics=['mse'])
        return model
    
class ActorNetwork(object):
    def __init__(self, TAU=0.001, LEARNING_RATE=0, pretrain_epoch=2, is_train=True, \
                 file_name='target_actor_model.h5'):
        if is_train:
            self.TAU = TAU
            self.LEARNING_RATE = LEARNING_RATE
            
            #Now create the model
            with tf.device("/cpu:0"):
                self.model= self.create_actor_network()   
                self.target_model= self.create_actor_network() 
            if not pretrain_epoch == 0:
                try:
                    self.model.load_weights('pretrained_actor_model.h5')
                    print("succesfully loaded the pretrained model")
                except:
                    print("start to pre train with greedy")
                    self.learn_rules(batch_size=512, epochs=pretrain_epoch)
                    self.model.save_weights('pretrained_actor_model.h5')
            self.update_target()
        else:
            try:
                self.target_model = load_model(file_name)
                print("successfully loaded trained target model")
            except:
                raise ValueError('Can not load target actor model')
    
    def save(self):
        self.target_model.save('target_actor_model.h5')
        print("target_model successfully saved")

    def update_target(self):
        actor_weights = self.model.get_weights()
        self.target_model.set_weights(actor_weights)

    def create_actor_network(self):
        board_input = Input(shape=(2, 7, 7))
        mask_input = Input(shape=(2, 7, 7))
        x = Conv2D(64, (3, 3), activation='relu', padding='same')(board_input)
        x = BatchNormalization(axis=1)(x)
        x = Conv2D(64, (3, 3), activation='relu', padding='same')(x)
        x = BatchNormalization(axis=1)(x)
        x = MaxPooling2D((2, 2))(x)
        
        x = Conv2D(128, (3, 3), activation='relu', padding='same')(x)
        x = BatchNormalization(axis=1)(x)
        x = Conv2D(128, (3, 3), activation='relu', padding='same')(x)
        x = BatchNormalization(axis=1)(x)
        x = Flatten()(x)
        
        x = Dense(98, activation='softplus')(x)
        x = Reshape((2, 7, 7))(x) 
        x = multiply(inputs=[x, mask_input])     # this mask will mask any illegal move
        x = Reshape((2, 49))(x)
        x = Activation('softmax')(x)
        x = Reshape((2, 7, 7))(x) 
        model = Model(input=[board_input, mask_input],output=[x])
        print(model.summary())
        # sgd = SGD(lr=self.LEARNING_RATE, decay=1e-6, momentum=0.9, nesterov=True, clipnorm=1.)
        model.compile(loss=neg_log_loss, optimizer=Adam(lr=self.LEARNING_RATE, decay=1e-6))
        return model
    
    def get_action_prob(self, feature_map, action_mask, is_target=False, get_batch=False):
        if not is_target:
            result = self.model.predict([np.reshape(feature_map, (-1, 2, 7, 7)), 
                                      np.reshape(action_mask, (-1, 2, 7, 7))])
        else:
            result = self.target_model.predict([np.reshape(feature_map, (-1, 2, 7, 7)), 
                                      np.reshape(action_mask, (-1, 2, 7, 7))])
        if get_batch:
            return result
        else:
            return result[0]
    
    def get_stochastic_action(self, feature_map, action_mask, is_target=False):
        # get action_prob
        action_prob = self.get_action_prob(feature_map, action_mask, is_target)
        # get valid_moves list
        game = Ataxx(board=feature_map[0] - feature_map[1])
        valid_moves = game.get_moves(1)
        index_list = range(len(valid_moves))
        # store pred prob for each valid moves and sort it
        valid_moves_prob = np.zeros(len(valid_moves))
        for i, move in enumerate(valid_moves):
            valid_moves_prob[i] = action_prob[0][move[0]] + action_prob[1][move[1]]
        # noramlize probablity
        valid_moves_prob = valid_moves_prob / valid_moves_prob.sum()
        # sample a policy according to predicted prob
        move_index = np.random.choice(range(len(valid_moves)), p=valid_moves_prob)
        move = valid_moves[move_index]
        # generate 7*7 pos map
        start_pos = np.zeros((7, 7))
        start_pos[move[0]] = 1
        end_pos = np.zeros((7, 7))
        end_pos[move[1]] = 1
        return move[0], move[1], np.concatenate((start_pos.reshape(1, 7, 7), end_pos.reshape(1, 7, 7)), axis=0)
    
    def get_batch_best_action(self, feature_map, action_mask, is_target=False):
        # calc batch size
        batch_size = feature_map.shape[0]
        # get action_prob
        action_prob = self.get_action_prob(feature_map, action_mask, is_target, get_batch=True)

        # get action map
        action_map = np.zeros(feature_map.shape)
        for k in range(batch_size):
            if feature_map[k].any():
                game = Ataxx(board=feature_map[k][0] - feature_map[k][1])
                valid_moves = game.get_moves(1)
                max_prob_sum = -1
                pos0 = (0, 0)
                pos1 = (0, 0)
                for move in valid_moves:
                    tmp_prob_sum = action_prob[k][0][move[0]] + action_prob[k][1][move[1]]
                    if tmp_prob_sum > max_prob_sum:
                        max_prob_sum = tmp_prob_sum
                        pos0 = move[0]
                        pos1 = move[1]
                action_map[k][0][pos0] = 1
                action_map[k][1][pos1] = 1
        return action_map
                
    
    def get_best_action(self, feature_map, action_mask, is_target=False, verbose=True):
        # get action_prob
        action_prob = self.get_action_prob(feature_map, action_mask, is_target)
        # get valid_moves list
        game = Ataxx(board=feature_map[0] - feature_map[1])
        valid_moves = game.get_moves(1)
        max_prob_sum = -1
        pos0 = (0, 0)
        pos1 = (0, 0)
        for move in valid_moves:
            tmp_prob_sum = action_prob[0][move[0]] + action_prob[1][move[1]]
            if tmp_prob_sum > max_prob_sum:
                max_prob_sum = tmp_prob_sum
                pos0 = move[0]
                pos1 = move[1]
        
        # output the max_prob
        if verbose:
            r = np.random.random()
            if r < 0.01:
                print("confidence of this best move is: ", max_prob_sum)
            
        # generate 7*7 pos map
        start_pos = np.zeros((7, 7))
        start_pos[pos0] = 1
        end_pos = np.zeros((7, 7))
        end_pos[pos1] = 1
        
        return pos0, pos1, np.concatenate((start_pos.reshape(1, 7, 7), end_pos.reshape(1, 7, 7)), axis=0)

    def data_generator(self, batch_size, max_size=10000):
        relay = Relay(max_size)
        game = Ataxx()
        turn = -1
        i = 0
        while True: 
            i += 1
            new_sample = []
            new_sample.append(game.get_feature_map(turn))
            new_sample.append(game.get_mask(turn))
            
            try:
                greedy_move = game.get_greedy_move(turn)
            except:
                game = Ataxx()
                turn = -1
                continue
            start_prob_map = np.zeros((7, 7))
            start_prob_map[greedy_move[0]] = 1
            end_prob_map = np.zeros((7, 7))
            end_prob_map[greedy_move[1]] = 1
                
            new_sample.append(np.concatenate((start_prob_map.reshape(1, 7, 7), end_prob_map.reshape(1, 7, 7)), axis=0))
            new_sample.extend([None, None, None])
            relay.add_sample(new_sample)
            
            move = choice(game.get_moves(turn))
            game.move_to(turn, move[0], move[1])
            turn = -turn
            
            if not i % 16 and relay.size() > batch_size*4:
                state, mask, action, _, _, _ = relay.get_batch(batch_size)
                yield [state, mask], action  
                
    def learn_rules(self, batch_size, epochs=10):
        tmp_game = Ataxx()
        print("trained action prob map predicted by initial model for a starting game")
        print(self.get_action_prob(tmp_game.get_feature_map(-1), tmp_game.get_mask(-1), is_target=True))
        sgd = SGD(lr=0.1, decay=1e-6, momentum=0.9, nesterov=True)
        gpu_model = multi_gpu_model(self.model, gpus=4)
        gpu_model.compile(loss='categorical_crossentropy', optimizer=sgd, metrics=['acc'])
        gpu_model.fit_generator(self.data_generator(batch_size), steps_per_epoch=256, epochs=epochs, 
                                    verbose=1,
                                    validation_data=self.data_generator(32), 
                                    validation_steps=1,
                                    workers=16,
                                    use_multiprocessing=True,
                                    callbacks=[ReduceLROnPlateau(cooldown=5, min_lr=0.01, patience=2)])
        
        # set target network and learning network to be the same
        self.update_target()
        
        tmp_game = Ataxx()
        print("trained action prob map predicted by initial model for a starting game")
        print(self.get_action_prob(tmp_game.get_feature_map(-1), tmp_game.get_mask(-1), is_target=True))

In [16]:
def reinforcement_learning(epochs=1000, check_point=True, step_per_epoch=50, \
                           BATCH_SIZE=64, TRAIN_BATCH_TIME=1, GAMMA=0.99, RELAY_SIZE=50000, TAU=0.001, LRA=0.0001, LRC=0.0001):        
    actor = ActorNetwork(TAU, LRA, 32)
    critic = CriticNetwork(TAU, LRC)
    relay = Relay(RELAY_SIZE)

    max_score = 1
    min_score = 0.001
    
    for ep in range(epochs):
        reward = 0
        step = 0

        game = Ataxx()
        turn = -1 # start turn is -1

        while abs(game.evaluate(turn, turn, max_score, min_score)) != max_score:
            new_sample = [] # prepare to collect new sample
            
            cur_feature = game.get_feature_map(turn)
            cur_mask = game.get_mask(turn)
            
            pos0, pos1, cur_action = actor.get_stochastic_action(cur_feature, cur_mask) # get proposed action
            
            # new_state = game.simu_move_to(turn, pos0, pos1)
            
            # create new_sample and add that to relay
            new_sample.append(cur_feature) # cur_state
            new_sample.append(cur_mask) # cur_mask
            new_sample.append(cur_action) # cur_action
            
            game.move_to(turn, pos0, pos1) # do the move here if the move is valid
            turn = -turn # the turn now is the next turn, what we are learning for is -turn
            
            new_sample.append(game.evaluate(-turn, turn, max_score, min_score)) # cur_reward
            if abs(new_sample[-1]) == max_score:
                new_sample.append(np.zeros((2, 7, 7))) 
                new_sample.append(np.zeros((2, 7, 7))) 
            else:
                new_sample.append(game.get_feature_map(turn)) # new_state
                new_sample.append(game.get_mask(turn)) # new_mask
                
            relay.add_sample(new_sample)
            step += 1
        
        print("Episode : " + str(ep) + " Replay Buffer " + str(relay.size()))
        print("TOTAL REWARD @ " + str(ep) +"-th Episode  : Reward " + str(game.evaluate(1, turn, max_score, min_score)))
        print("Total Step: " + str(step))
        
        #Do the batch update....if possible
        if relay.size() > BATCH_SIZE * 2:
            for t in range(step_per_epoch):
                cur_state, cur_mask, cur_action, \
                    cur_reward, new_state, new_mask = relay.get_batch(BATCH_SIZE)
                q_target = cur_reward
                critic_sample_weight = np.ones(BATCH_SIZE)
                
                # set bias training weight and store all new actions
                bias_sample_weight = 10
                new_action = np.zeros((BATCH_SIZE, 2, 7, 7))
                not_end_of_game = np.ones(BATCH_SIZE)
                
                # using batch action prediction leads to a 5 times improvement in speed
                print("start searching new action")
                start = time.time()
                # generate new action using target model
                new_action = actor.get_batch_best_action(new_state, new_mask, is_target=True)
                for k in range(BATCH_SIZE):
                    if not new_state[k].any():
                        critic_sample_weight[k] = bias_sample_weight
                        not_end_of_game[k] = 0
                print("get new action: ", time.time()-start)            
                  
                print("start getting new_q")
                start = time.time()
                q_new = critic.target_model.predict([new_state, new_action]).reshape(BATCH_SIZE)
                q_target += - GAMMA*not_end_of_game*q_new
                # log loss update weight equal to critic output    
                actor_sample_weight = q_target
                print("get new_q: ", time.time()-start)            
                 
                print("train start:")
                start = time.time()
                # train models
                for nb in range(TRAIN_BATCH_TIME):
                    print("critic loss", critic.model.train_on_batch([cur_state, cur_action], q_target,\
                                                                     sample_weight=critic_sample_weight))
                if not critic.pretrained:
                    if ep == 150:
                        critic.save_target_pretrain()
                        critic.pretrained = True
                else:
                    print("actor loss", actor.model.train_on_batch([cur_state, cur_mask], cur_action,\
                                                                    sample_weight=actor_sample_weight))
                # update target critic models slowly for stability
                critic.target_train()
                print("train end", time.time()-start)
                
                for k in range(BATCH_SIZE):
                    if not_end_of_game[k] == 0:
                        q_p = critic.model.predict([cur_state[k].reshape(1, 2, 7, 7), \
                                             cur_action[k].reshape(1, 2, 7, 7)])[0]
                        q_p_t = critic.target_model.predict([cur_state[k].reshape(1, 2, 7, 7), \
                                             cur_action[k].reshape(1, 2, 7, 7)])[0]
                        print("should be {}, predicted: {}, target predicted: {}".format(q_target[k], q_p, q_p_t))
        
                        
        # performance checking
        if (ep + 1) % 10 == 0:
            tmp_game = Ataxx()
            print("trained action prob map predicted by initial model for a starting game")
            print(actor.get_action_prob(tmp_game.get_feature_map(-1), tmp_game.get_mask(-1), is_target=False))
        
        # update and check point model
        if (ep+1) % 300 == 0:
            actor.update_target()
            if check_point:
                actor.save()

    print("Finish.")
    actor.save()
    return actor

## Ideas:
1. when comes to new state in training, we should make sure we use target network for both actor and crtic model, in order to have more stability
2. We might will need to keep relay_size smaller so that actor can always learn on a more recent version of target actor network
3. Normalizing that action probability so that the chosen action becomes 1 while other actions becomes 0 is reasonable, because firstly, it makes it easier for crtic model to get a stable output and maintain the property of discrete policys, at least a same critic output for the same choice of policy, secondly, it still helps the guiding of the training on policy model, cuz bad gradient still will be passed if the critic output is bad, and as long as we train for only a few times (maybe one is the most reasonable one..), the property of discrete policy maintains even if we do not change the action mask. 
4. The confidence of the target model of its prediction seems to be a good indication for convergence, cuz that's the only indicator that is monotonic during the training process。。。。
5. The natural phenomenom of training is that, in the begining, loss for actor is close to 0, as critic is just initialized and its output will always be that. For a while, constant increase will be observed in actor loss, as critic is starting to learn larger values while actor is still basically a random picker. After a while, when critic loss has decreased a lot, actor loss should also start to decrease, and this period should be the actual training for actor model.
6. During training, it can be helpful to set the sample weight for 1 and -1 to be very large, cuz it is (1)the hardest to learn considering the around zero init, and (2) most important way to understand rules
7. Setting learning rate for critic to be higher might be reasonable as it helps q converge faster


In [17]:
actor = reinforcement_learning(epochs=2000, check_point=True, step_per_epoch=8, 
                               RELAY_SIZE=50000, BATCH_SIZE=256, TRAIN_BATCH_TIME=5, LRC=5e-5, LRA=1e-5, TAU=0.01)

/home/yuze/anaconda3/envs/tensorflow/lib/python3.5/site-packages/ipykernel_launcher.py:125: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outputs=[<tf.Tenso..., inputs=[<tf.Tenso...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_17 (InputLayer)           (None, 2, 7, 7)      0                                            
__________________________________________________________________________________________________
conv2d_37 (Conv2D)              (None, 64, 7, 7)     1216        input_17[0][0]                   
__________________________________________________________________________________________________
batch_normalization_41 (BatchNo (None, 64, 7, 7)     256         conv2d_37[0][0]                  
__________________________________________________________________________________________________
conv2d_38 (Conv2D)              (None, 64, 7, 7)     36928       batch_normalization_41[0][0]     
__________________________________________________________________________________________________
batch_norm

succesfully loaded the pretrained model
actor
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_21 (InputLayer)           (None, 2, 7, 7)      0                                            
__________________________________________________________________________________________________
input_22 (InputLayer)           (None, 2, 7, 7)      0                                            
__________________________________________________________________________________________________
concatenate_5 (Concatenate)     (None, 4, 7, 7)      0           input_21[0][0]                   
                                                                 input_22[0][0]                   
__________________________________________________________________________________________________
conv2d_47 (Conv2D)              (None, 64, 7, 7)     2368      

get new action:  0.2520325183868408
start getting new_q
get new_q:  0.11342000961303711
train start:
critic loss [1.3358223, 1.2515056]
critic loss [1.2063838, 1.160249]
critic loss [1.0532249, 1.0417418]
critic loss [0.91222358, 0.91154212]
critic loss [0.79160774, 0.78028774]
train end 0.5057463645935059
should be -1.0, predicted: [ 0.10907055], target predicted: [-0.12805255]
should be 1.0, predicted: [ 0.14058764], target predicted: [-0.02119489]
should be 1.0, predicted: [ 0.15637663], target predicted: [-0.02856207]
start searching new action
get new action:  0.2661299705505371
start getting new_q
get new_q:  0.06645941734313965
train start:
critic loss [1.2614779, 1.0255499]
critic loss [1.129199, 0.96823466]
critic loss [0.9662025, 0.89033115]
critic loss [0.81950957, 0.80136907]
critic loss [0.7093209, 0.70720041]
train end 0.46562671661376953
should be 1.0, predicted: [ 0.16327415], target predicted: [-0.07336703]
should be 1.0, predicted: [ 0.18231045], target predicted: [-0

get new action:  0.2458515167236328
start getting new_q
get new_q:  0.06366276741027832
train start:
critic loss [0.84237397, 0.57035613]
critic loss [0.74564892, 0.54679704]
critic loss [0.61577284, 0.51159662]
critic loss [0.50715673, 0.47406667]
critic loss [0.4428159, 0.43820542]
train end 0.40228748321533203
should be 1.0, predicted: [ 0.47366878], target predicted: [ 0.05413502]
should be 1.0, predicted: [ 0.52335656], target predicted: [ 0.05730252]
should be -1.0, predicted: [ 0.32819316], target predicted: [ 0.00787585]
start searching new action
get new action:  0.24584102630615234
start getting new_q
get new_q:  0.06182050704956055
train start:
critic loss [0.69057548, 0.59463328]
critic loss [0.65726012, 0.58100361]
critic loss [0.59559965, 0.54678607]
critic loss [0.52196765, 0.49901429]
critic loss [0.45123568, 0.44521347]
train end 0.392214298248291
should be 1.0, predicted: [ 0.44841358], target predicted: [ 0.03739609]
start searching new action
get new action:  0.2466

...

Episode : 1173 Replay Buffer 50000
TOTAL REWARD @ 1173-th Episode  : Reward 1
Total Step: 186
start searching new action
get new action:  0.2290782928466797
start getting new_q
get new_q:  0.06722044944763184
train start:
critic loss [0.003638471, 0.0035439108]
critic loss [0.0033967651, 0.0033316256]
critic loss [0.0031960073, 0.0031593582]
critic loss [0.0030557083, 0.0030410066]
critic loss [0.0029744697, 0.0029720208]
actor loss nan
train end 0.5304536819458008
should be 1.0, predicted: [ 1.11002636], target predicted: [ 0.99855512]
start searching new action
get new action:  0.20797228813171387
start getting new_q
get new_q:  0.06840658187866211
train start:
critic loss [0.0013790054, 0.0011261504]
critic loss [0.0014857557, 0.0011922002]
critic loss [0.0014283108, 0.0011647976]
critic loss [0.0012396385, 0.0010568141]
critic loss [0.00099892181, 0.00090645393]
actor loss nan
train end 0.5095870494842529
should be 1.0, predicted: [ 1.05488074], target predicted: [ 1.01455271]
shou

critic loss [0.00042682665, 0.00042682665]
critic loss [0.00034276705, 0.00034276705]
actor loss nan
train end 0.6239204406738281
start searching new action
get new action:  0.22012996673583984
start getting new_q
get new_q:  0.07381343841552734
train start:
critic loss [0.0043586064, 0.0043586064]
critic loss [0.0043206038, 0.0043206038]
critic loss [0.003981675, 0.003981675]
critic loss [0.0034548901, 0.0034548901]
critic loss [0.0028752144, 0.0028752144]
actor loss nan
train end 0.68678879737854
start searching new action
get new action:  0.22983145713806152
start getting new_q
get new_q:  0.07631993293762207
train start:
critic loss [0.0067217182, 0.0064895563]
critic loss [0.0061818222, 0.0059623243]
critic loss [0.0057306755, 0.0055439118]
critic loss [0.0054081245, 0.0052662971]
critic loss [0.0052206642, 0.0051226243]
actor loss nan
train end 0.6114988327026367
should be 1.0, predicted: [ 1.02852452], target predicted: [ 1.01745546]
start searching new action
get new action:  0

get new action:  0.23708415031433105
start getting new_q
get new_q:  0.07388734817504883
train start:
critic loss [0.0012716691, 0.0012657929]
critic loss [0.0010113145, 0.0010064754]
critic loss [0.00077108154, 0.00076769013]
critic loss [0.00058607379, 0.00058411789]
critic loss [0.00047619478, 0.00047536567]
actor loss nan
train end 0.6563844680786133
should be 1.0, predicted: [ 0.95471066], target predicted: [ 0.99234682]
start searching new action
get new action:  0.2159252166748047
start getting new_q
get new_q:  0.07383418083190918
train start:
critic loss [0.0024801183, 0.0024397504]
critic loss [0.0026711235, 0.0026336282]
critic loss [0.0026278924, 0.0025950987]
critic loss [0.0023769555, 0.0023499047]
critic loss [0.0019893537, 0.0019682338]
actor loss nan
train end 0.5663590431213379
should be 1.0, predicted: [ 0.96146441], target predicted: [ 0.99573278]
start searching new action
get new action:  0.21525168418884277
start getting new_q
get new_q:  0.06676506996154785
trai

get new action:  0.21790242195129395
start getting new_q
get new_q:  0.06296038627624512
train start:
critic loss [0.0028454801, 0.0028454801]
critic loss [0.0021993639, 0.0021993639]
critic loss [0.00157927, 0.00157927]
critic loss [0.0010946628, 0.0010946628]
critic loss [0.000792932, 0.000792932]
actor loss nan
train end 0.5931017398834229
start searching new action
get new action:  0.22494292259216309
start getting new_q
get new_q:  0.06324052810668945
train start:
critic loss [0.0041898382, 0.0040059602]
critic loss [0.0043581827, 0.004173758]
critic loss [0.0044557145, 0.0042850985]
critic loss [0.0044451384, 0.0042995531]
critic loss [0.0043208115, 0.004206812]
actor loss nan
train end 0.5944252014160156
should be 1.0, predicted: [ 0.98867297], target predicted: [ 0.99031293]
start searching new action
get new action:  0.22285795211791992
start getting new_q
get new_q:  0.06232118606567383
train start:
critic loss [0.0018292367, 0.0015884687]
critic loss [0.0016891879, 0.0015016

KeyboardInterrupt: 

In [50]:
graph = 0

def reinforcement_data_generator(actor_model, actor_target, critic_model, critic_target, relay, \
                                 train_critic=True, step_per_episode=50, \
                                 BATCH_SIZE=64, GAMMA=0.99, RELAY_SIZE=10000): 
    global graph
    with graph.as_default():
        max_score = 1
        min_score = 0.02
        policy_mask_init = 0.01

        actor = ActorNetwork(target_model=actor_target, model=actor_model)
        critic = CriticNetwork(target_model=critic_target, model=actor_model)
        print("actor critic prepared")

        while True:
            reward = 0
            step = 0

            game = Ataxx()
            turn = -1 # start turn is -1

            while abs(game.evaluate(turn, turn, max_score, min_score)) != max_score:
                new_sample = [] # prepare to collect new sample

                pos0, pos1, cur_action_mask = actor.get_noised_action(game, turn, epsilon=0.1, mask_init=policy_mask_init, verbose=0) # get proposed action

                new_state = game.simu_move_to(turn, pos0, pos1)

                # create new_sample and add that to relay
                new_sample.append(game.get_feature_map(turn)) # cur_state
                new_sample.append(game.get_mask(turn)) # cur_mask
                new_sample.append(actor.get_action_prob(game, turn)) # cur_action
                new_sample.append(cur_action_mask) # cur_action_mask

                game.move_to(turn, pos0, pos1) # do the move here if the move is valid
                turn = -turn # the turn now is the next turn, what we are learning for is -turn

                new_sample.append(game.evaluate(-turn, turn, max_score, min_score)) # cur_reward
                if abs(new_sample[-1]) == max_score:
                    new_sample.append(None) 
                else:
                    new_sample.append(game.get_feature_map(turn)) # new_state

                relay.add_sample(new_sample)

            if relay.size() > BATCH_SIZE:
                for t in range(step_per_episode):
                    cur_state, cur_mask, cur_action, cur_action_mask, \
                        cur_reward, new_state = relay.get_batch(BATCH_SIZE)
                    q_target = np.zeros(BATCH_SIZE)

                    for k in range(BATCH_SIZE):
                        if new_state[k] is None:
                            q_target[k] = cur_reward[k]
                        else:
                            # generate new action
                            board = new_state[k][0] - new_state[k][1]
                            tmp_game = Ataxx(board) # recover the game board

                            new_action, new_action_mask = actor.get_noised_action(tmp_game, 1, epsilon=0, return_position=False, 
                                                                        mask_init=policy_mask_init, is_target=True, verbose=False)
                            q_new = critic.target_model.predict([new_state[k].reshape(1, 2, 7, 7), 
                                                                new_action.reshape(1, 2, 7, 7),
                                                                new_action_mask.reshape(1, 2, 7, 7)])[0]
                            q_target[k] = cur_reward[k] - GAMMA*q_new # cuz this q_new is for the opponent
                    if train_critic:
                        yield [cur_state, cur_action, cur_action_mask], q_target
                    else:
                        yield [cur_state, cur_mask, cur_action_mask], np.zeros(BATCH_SIZE)

def actor_critic_trainer(epochs=1000, check_point=True, steps_per_epoch=50, \
                           BATCH_SIZE=64, TRAIN_BATCH_TIME=1, GAMMA=0.99, RELAY_SIZE=10000, TAU=0.001, LRA=0.0001, LRC=0.0001): 
    actor = ActorNetwork(TAU, LRA, 0)
    critic = CriticNetwork(TAU, LRC)
    relay = Relay(RELAY_SIZE)
    global graph
    graph = tf.get_default_graph()

    with tf.device('/cpu'):
        actor_critic_model = Model(inputs=[actor.model.inputs[0], actor.model.inputs[1], critic.frozen_model.inputs[2]],
                                   outputs=[critic.frozen_model([actor.model.inputs[0], actor.model.outputs[0], critic.frozen_model.inputs[2]])])
        sgd = SGD(lr=LRA, decay=5e-7, momentum=0.9, nesterov=True)
        actor_critic_model.compile(loss=neg_linear_loss, optimizer=sgd)
    gpu_ac_model = multi_gpu_model(actor_critic_model, gpus=4)
    gpu_ac_model.compile(loss=neg_linear_loss, optimizer=Adam(lr=LRA))
    print(gpu_ac_model.summary())
    
    for ep in range(epochs):
        critic.gpu_model.fit_generator(reinforcement_data_generator(actor.model, actor.target_model, \
                                                                    critic.model, critic.target_model, \
                                                                    relay, train_critic=True, \
                                                                    step_per_episode=50, \
                                                                    BATCH_SIZE=256, GAMMA=0.99, RELAY_SIZE=RELAY_SIZE),\
                                       verbose=1, steps_per_epoch=steps_per_epoch, \
                                       #workers=8, use_multiprocessing=True
                                      )
        gpu_ac_model.fit_generator(reinforcement_data_generator(actor.model, actor.target_model, \
                                                                critic.model, critic.target_model, \
                                                                relay, train_critic=False, \
                                                                step_per_episode=50, \
                                                                BATCH_SIZE=256, GAMMA=0.99, RELAY_SIZE=RELAY_SIZE),\
                                   verbose=1, steps_per_epoch=steps_per_epoch, \
                                   #workers=8, use_multiprocessing=True
                                  )
        actor.target_train()
        critic.target_train()
        
        if check_point:
            actor.save()
        tmp_game = Ataxx()
        print("trained action prob map predicted by initial model for a starting game")
        print(actor.get_action_prob(tmp_game, -1, is_target=True))

In [51]:
actor_critic_trainer(epochs=1000, check_point=True, steps_per_epoch=50, \
                     BATCH_SIZE=64, TRAIN_BATCH_TIME=1, GAMMA=0.99, RELAY_SIZE=10000, \
                     TAU=0.001, LRA=0.0001, LRC=0.0001) 
    

/home/yuze/anaconda3/envs/tensorflow/lib/python3.5/site-packages/ipykernel_launcher.py:121: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outputs=[<tf.Tenso..., inputs=[<tf.Tenso...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_153 (InputLayer)          (None, 2, 7, 7)      0                                            
__________________________________________________________________________________________________
conv2d_242 (Conv2D)             (None, 64, 5, 5)     1216        input_153[0][0]                  
__________________________________________________________________________________________________
batch_normalization_271 (BatchN (None, 64, 5, 5)     256         conv2d_242[0][0]                 
__________________________________________________________________________________________________
conv2d_243 (Conv2D)             (None, 64, 5, 5)     36928       batch_normalization_271[0][0]    
__________________________________________________________________________________________________
batch_norm

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_161 (InputLayer)          (None, 2, 7, 7)      0                                            
__________________________________________________________________________________________________
input_162 (InputLayer)          (None, 2, 7, 7)      0                                            
__________________________________________________________________________________________________
multiply_64 (Multiply)          (None, 2, 7, 7)      0           input_161[0][0]                  
                                                                 input_162[0][0]                  
__________________________________________________________________________________________________
input_160 (InputLayer)          (None, 2, 7, 7)      0                                            
__________

50/50 [==============================] - 127s 3s/step - loss: 1.9434 - mean_squared_error: 1.9434


Exception ignored in: <generator object reinforcement_data_generator at 0x7f765f58e468>
Traceback (most recent call last):
  File "<ipython-input-50-b196c6d99be7>", line 67, in reinforcement_data_generator
  File "/home/yuze/anaconda3/envs/tensorflow/lib/python3.5/contextlib.py", line 77, in __exit__
    self.gen.throw(type, value, traceback)
  File "/home/yuze/.local/lib/python3.5/site-packages/tensorflow/python/framework/ops.py", line 4342, in get_controller
    if self.stack[-1] is not default:
IndexError: list index out of range


...

Exception ignored in: <generator object reinforcement_data_generator at 0x7f7653a4b1a8>
Traceback (most recent call last):
  File "<ipython-input-50-b196c6d99be7>", line 67, in reinforcement_data_generator
  File "/home/yuze/anaconda3/envs/tensorflow/lib/python3.5/contextlib.py", line 77, in __exit__
    self.gen.throw(type, value, traceback)
  File "/home/yuze/.local/lib/python3.5/site-packages/tensorflow/python/framework/ops.py", line 4342, in get_controller
    if self.stack[-1] is not default:
IndexError: list index out of range


trained action prob map predicted by initial model for a starting game
[[[ 0.02044491  0.0204074   0.0204074   0.0204074   0.0204074   0.0204074
    0.0204074 ]
  [ 0.0204074   0.0204074   0.0204074   0.0204074   0.0204074   0.0204074
    0.0204074 ]
  [ 0.0204074   0.0204074   0.0204074   0.0204074   0.0204074   0.0204074
    0.0204074 ]
  [ 0.0204074   0.0204074   0.0204074   0.0204074   0.0204074   0.0204074
    0.0204074 ]
  [ 0.0204074   0.0204074   0.0204074   0.0204074   0.0204074   0.0204074
    0.0204074 ]
  [ 0.0204074   0.0204074   0.0204074   0.0204074   0.0204074   0.0204074
    0.0204074 ]
  [ 0.0204074   0.0204074   0.0204074   0.0204074   0.0204074   0.0204074
    0.0204074 ]]

 [[ 0.02039324  0.02046709  0.02065576  0.02039324  0.02039324  0.02039324
    0.02039324]
  [ 0.02040218  0.02039324  0.02043024  0.02039324  0.02039324  0.02039324
    0.02039324]
  [ 0.02039324  0.02039324  0.02040604  0.02039324  0.02039324  0.02039324
    0.02039324]
  [ 0.02039324  0.020393

Exception ignored in: <generator object reinforcement_data_generator at 0x7f7653a4b0f8>
Traceback (most recent call last):
  File "<ipython-input-50-b196c6d99be7>", line 67, in reinforcement_data_generator
  File "/home/yuze/anaconda3/envs/tensorflow/lib/python3.5/contextlib.py", line 77, in __exit__
    self.gen.throw(type, value, traceback)
  File "/home/yuze/.local/lib/python3.5/site-packages/tensorflow/python/framework/ops.py", line 4342, in get_controller
    if self.stack[-1] is not default:
IndexError: list index out of range


actor critic prepared
Epoch 1/1
49/50 [============================>.] - ETA: 1s - loss: -3.6208e-09

KeyboardInterrupt: 